<a href="https://colab.research.google.com/github/alfredcs/AWSabs/blob/master/Fine_Tune_Llama_3_2_Vision_Language_Model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Fine-tuning Llama 3.2 Vision-Language Model for Product Description Generation

## 1. Introduction
(Add your introduction text here)

## 2. Setting Up the Environment

First, let's install the necessary libraries:

In [ ]:
!pip install "torch==2.4.0" tensorboard pillow torchvision accelerate huggingface_hub
!pip install --upgrade \
 "transformers==4.45.1" \
 "datasets==3.0.1" \
 "accelerate==0.34.2" \
 "evaluate==0.4.3" \
 "bitsandbytes==0.44.0" \
 "trl==0.11.1" \
 "peft==0.13.0" \
 "qwen_vl_utils"

Now, let's import the required libraries:

In [ ]:
print('hello world')

hello world


In [ ]:
import torch
from transformers import AutoProcessor, AutoTokenizer, AutoModelForCausalLM
#from unsloth import FastLanguageModel
from peft import LoraConfig, PeftModel, PeftConfig
from trl import SFTTrainer, SFTConfig
from datasets import load_dataset
from huggingface_hub import HfApi
from PIL import Image
import requests

## 3. Preparing the Dataset

We'll use the Amazon Product Descriptions VLM dataset:

In [ ]:
dataset_id = "akritRihal/Indian_Sign_Language_dataset"
dataset = load_dataset(dataset_id, split="train")
print(dataset)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/1.07k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/440M [00:00<?, ?B/s]

test-00000-of-00001.parquet:   0%|          | 0.00/76.8M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/9139 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1613 [00:00<?, ? examples/s]

Dataset({
    features: ['image', 'label'],
    num_rows: 9139
})


In [ ]:
prompt = """I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image."""

system_message = "You are an expert sign language detector"

def format_data(sample):
    return {"messages": [
        # {
        #     "role": "system",
        #     "content": [{"type": "text", "text": system_message}],
        # },
        {
            "role": "user",
            "content": [
                {
                    "type": "text",
                    "text": prompt,
                },{
                    "type": "image",
                    "image": sample["image"],
                }
            ],
        },
        {
            "role": "assistant",
            "content": [{"type": "text", "text": sample["label"]}],
        },
    ],
    }

dataset_id = "akritRihal/Indian_Sign_Language_dataset"
dataset = load_dataset(dataset_id, split="train")
dataset = [format_data(sample) for sample in dataset]

## 4. Fine-Tuning VLMs Using TRL, SFTTrainer, and Unsloth

### Initialize the Llama 3.2 Vision Model with Unsloth

In [ ]:
print(dataset[345]["messages"])

[{'role': 'user', 'content': [{'type': 'text', 'text': 'I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image.'}, {'type': 'image', 'image': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=191x186 at 0x7E8869C39480>}]}, {'role': 'assistant', 'content': [{'type': 'text', 'text': 0}]}]


In [ ]:
print(dataset[344])

{'messages': [{'role': 'user', 'content': [{'type': 'text', 'text': 'I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image.'}, {'type': 'image', 'image': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=95x90 at 0x7E8869C3B0A0>}]}, {'role': 'assistant', 'content': [{'type': 'text', 'text': 28}]}]}


In [ ]:
load_dataset(dataset_id, split="train")

Dataset({
    features: ['image', 'label'],
    num_rows: 9139
})

In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: write).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in 

In [ ]:
import torch
from transformers import AutoModelForVision2Seq, AutoProcessor, BitsAndBytesConfig

# Hugging Face model id
model_id = "meta-llama/Llama-3.2-11B-Vision-Instruct"

# BitsAndBytesConfig int-4 config
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True, bnb_4bit_use_double_quant=True, bnb_4bit_quant_type="nf4", bnb_4bit_compute_dtype=torch.bfloat16
)

# Load model and tokenizer
model = AutoModelForVision2Seq.from_pretrained(
    model_id,
    device_map="auto",
    # attn_implementation="flash_attention_2", # not supported for training
    torch_dtype=torch.bfloat16,
    quantization_config=bnb_config
)
processor = AutoProcessor.from_pretrained(model_id)



config.json:   0%|          | 0.00/5.07k [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/89.4k [00:00<?, ?B/s]

model-00001-of-00005.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00002-of-00005.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

model-00003-of-00005.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

...

preprocessor_config.json:   0%|          | 0.00/437 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/55.8k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/454 [00:00<?, ?B/s]

chat_template.json:   0%|          | 0.00/5.15k [00:00<?, ?B/s]

In [ ]:
dataset

[{'messages': [{'role': 'user',
    'content': [{'type': 'text',
      'text': 'I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image.'},
     {'type': 'image',
      'image': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=185x180>}]},
   {'role': 'assistant', 'content': [{'type': 'text', 'text': 19}]}]},
 {'messages': [{'role': 'user',
    'content': [{'type': 'text',
      'text': 'I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image.'},
     {'type': 'image',
      'image': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=205x200>}]},
   {'role': 'assistant', 'content': [{'type': 'text', 'text': 9}]}]},
 {'messages': [{'role': 'user',
    'content': [{'type': 'text',
      'text': 'I am providing you an image and tell me which sign language All the images 

In [ ]:
text = processor.apply_chat_template(
    dataset[2]["messages"], tokenize=False, add_generation_prompt=False
)

In [ ]:
print(text)

In [ ]:
# import torch
# from transformers import AutoProcessor
# from unsloth import FastLanguageModel

# model_id = "meta-llama/Llama-3.2-11B-Vision-Instruct"

# # Initialize the model with Unsloth
# model, tokenizer = FastLanguageModel.from_pretrained(
#     model_name=model_id,
#     max_seq_length=2048,
#     dtype=torch.bfloat16,
#     load_in_4bit=True,
# )

# processor = AutoProcessor.from_pretrained(model_id)

### Set Up LoRA Configuration for Fine-Tuning

In [ ]:
peft_config = LoraConfig(
    lora_alpha=16,
    lora_dropout=0.05,
    r=8,
    bias="none",
    target_modules=["q_proj", "v_proj"],
    task_type="CAUSAL_LM"
)

### Training Configuration

In [ ]:
from trl import SFTConfig

args = SFTConfig(
    output_dir="fine-tuned-visionllama-unsloth",
    num_train_epochs=3,
    per_device_train_batch_size=4,
    gradient_accumulation_steps=8,
    gradient_checkpointing=True,
    optim="adamw_torch_fused",
    logging_steps=5,
    save_strategy="epoch",
    learning_rate=2e-4,
    bf16=True,
    max_grad_norm=0.3,
    warmup_ratio=0.03,
    lr_scheduler_type="constant",
    push_to_hub=True,
    report_to="tensorboard",
    dataset_kwargs={"skip_prepare_dataset": True},
)

### Collate Data and Train the Model

In [ ]:
from datasets import Dataset
Dataset.from_list(dataset)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/datasets/arrow_writer.py", line 188, in __arrow_array__
    out = pa.array(cast_to_python_objects(data, only_1d_for_numpy=True))
  File "pyarrow/array.pxi", line 368, in pyarrow.lib.array
  File "pyarrow/array.pxi", line 42, in pyarrow.lib._sequence_to_array
  File "pyarrow/error.pxi", line 155, in pyarrow.lib.pyarrow_internal_check_status
  File "pyarrow/error.pxi", line 92, in pyarrow.lib.check_status
pyarrow.lib.ArrowInvalid: Could not convert <PIL.PngImagePlugin.PngImageFile image mode=RGB size=185x180 at 0x7E8869951030> with type PngImageFile: did not recognize Python value type when inferring an Arrow data type

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/PIL/ImageFile.py", line 547, in _save
    fh = fp.fileno()
AttributeError: '_idat' object has no attribute 'fileno'

During handling of the

TypeError: object of type 'NoneType' has no len()

In [ ]:
mock_examples = [
    {"messages": [{"role": "user", "content": "Sample message 1"}]},
    {"messages": [{"role": "user", "content": "Sample message 2"}]},
    {"messages": [{"role": "user", "content": "Sample message 3"}]},
    {"messages": [{"role": "user", "content": "Sample message 4"}]}
]


# Test collate_fn with mock data
print(collate_fn(mock_examples))


Examples: [{'messages': [{'role': 'user', 'content': 'Sample message 1'}]}, {'messages': [{'role': 'user', 'content': 'Sample message 2'}]}, {'messages': [{'role': 'user', 'content': 'Sample message 3'}]}, {'messages': [{'role': 'user', 'content': 'Sample message 4'}]}]


ValueError: Invalid input type. Must be a single image, a list of images, or a list of batches of images.

In [ ]:
from qwen_vl_utils import process_vision_info

def collate_fn(examples):
    print(examples)
    texts = [processor.apply_chat_template(example["messages"], tokenize=False) for example in examples]
    image_inputs = [process_vision_info(example["messages"])[0]]
    for example in examples:
        batch = processor(text=texts, images=image_inputs, return_tensors="pt", padding=True)
        labels = batch["input_ids"].clone()
        labels[labels == processor.tokenizer.pad_token_id] = -100

        image_tokens = [processor.tokenizer.convert_tokens_to_ids(processor.image_token)]
        for image_token_id in image_tokens:
            labels[labels == image_token_id] = -100
        batch["labels"] = labels

    return batch

trainer = SFTTrainer(
    model=model,
    args=args,
    train_dataset=dataset,
    data_collator=collate_fn(dataset),
    tokenizer=processor.tokenizer, # Use the tokenizer from Unsloth
    peft_config=peft_config
)

# # Apply Unsloth optimizations
# trainer = FastLanguageModel.get_peft_model(
#     trainer,
#     r=8,
#     target_modules=["q_proj", "v_proj"],
#     lora_alpha=16,
#     lora_dropout=0.05,
#     bias="none",
#     use_gradient_checkpointing=True,
#     random_state=3407,
#     use_rslora=False,
#     loftq_config=None,
# )

trainer.train()

Examples: [{'messages': [{'role': 'user', 'content': [{'type': 'text', 'text': 'I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image.'}, {'type': 'image', 'image': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=185x180 at 0x7E8869951030>}]}, {'role': 'assistant', 'content': [{'type': 'text', 'text': 19}]}]}, {'messages': [{'role': 'user', 'content': [{'type': 'text', 'text': 'I am providing you an image and tell me which sign language All the images are either english alphabets or Numbers so select between these options only using image.'}, {'type': 'image', 'image': <PIL.PngImagePlugin.PngImageFile image mode=RGB size=205x200 at 0x7E8869950040>}]}, {'role': 'assistant', 'content': [{'type': 'text', 'text': 9}]}]}, {'messages': [{'role': 'user', 'content': [{'type': 'text', 'text': 'I am providing you an image and tell me which sign language All the images are either eng

## 5. Saving the Fine-Tuned Model

### Saving PEFT Weights

In [ ]:
peft_model = trainer.model
output_dir = "path/to/save/peft_weights"
peft_model.save_pretrained(output_dir)

### Saving the Tokenizer

In [ ]:
tokenizer.save_pretrained(output_dir)

### Pushing to Hugging Face Hub (Optional)

In [ ]:
api = HfApi()
api.upload_folder(
    folder_path=output_dir,
    repo_id="your-username/your-model-name",
    repo_type="model"
)

## 6. Loading the Fine-Tuned Model for Inference

### Loading the Base Model and PEFT Weights

In [ ]:
base_model_id = "meta-llama/Llama-3.2-11B-Vision-Instruct"
base_model = AutoModelForCausalLM.from_pretrained(base_model_id)

peft_model_id = "path/to/saved/peft_weights"
config = PeftConfig.from_pretrained(peft_model_id)

model = PeftModel.from_pretrained(base_model, peft_model_id)

tokenizer = AutoTokenizer.from_pretrained(peft_model_id)
processor = AutoProcessor.from_pretrained(base_model_id)

### Preparing the Model for Inference

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
model.eval()
model.to(device)

### Example Inference

In [ ]:
image_url = "https://example.com/path/to/product_image.jpg"
image = Image.open(requests.get(image_url, stream=True).raw)

product_name = "Ergonomic Office Chair"
category = "Furniture"

prompt = f"""Create a Short Product description based on the provided ##PRODUCT NAME## and ##CATEGORY## and image.
Only return description. The description should be SEO optimized and for a better mobile search experience.

##PRODUCT NAME##: {product_name}
##CATEGORY##: {category}"""

inputs = processor(text=prompt, images=image, return_tensors="pt").to(device)

with torch.no_grad():
    outputs = model.generate(
        **inputs,
        max_new_tokens=100,
        do_sample=True,
        temperature=0.7,
        top_p=0.9,
    )

generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)

print("Generated Product Description:")
print(generated_text)